In [3]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [4]:
%%bash
# Install ViZDoom deps from
# https://github.com/mwydmuch/ViZDoom/blob/master/doc/Building.md#-linux

sudo apt update

apt-get install build-essential zlib1g-dev libsdl2-dev libjpeg-dev \
nasm tar libbz2-dev libgtk2.0-dev cmake git libfluidsynth-dev libgme-dev \
libopenal-dev timidity libwildmidi-dev unzip ffmpeg

# Boost libraries
apt-get install libboost-all-dev

# Lua binding dependencies
apt-get install liblua5.1-dev

Get:1 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Get:2 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,632 B]
Get:3 https://r2u.stat.illinois.edu/ubuntu jammy InRelease [6,555 B]
Hit:4 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:5 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease [1,581 B]
Get:6 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ Packages [83.6 kB]
Get:7 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [128 kB]
Get:8 http://security.ubuntu.com/ubuntu jammy-security/universe amd64 Packages [1,286 kB]
Get:9 http://security.ubuntu.com/ubuntu jammy-security/restricted amd64 Packages [6,008 kB]
Get:10 https://r2u.stat.illinois.edu/ubuntu jammy/main all Packages [9,491 kB]
Get:11 http://security.ubuntu.com/ubuntu jammy-security/main amd64 Packages [3,535 kB]
Get:12 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease [18.1 kB]
Hit:13 https://ppa.laun



W: Skipping acquire of configured file 'main/source/Sources' as repository 'https://r2u.stat.illinois.edu/ubuntu jammy InRelease' does not seem to provide it (sources.list entry misspelt?)


In [5]:
# install python libraries
# thanks toinsson
!pip install faster-fifo==1.4.2
!pip install vizdoom

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.6/84.6 kB 3.3 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for faster-fifo: filename=faster_fifo-1.4.2-cp311-cp311-linux_x86_64.whl size=329313 sha256=8d108c59fd5f9c356d3c62961c562ced5e6b7d284824333889a653d85158cd51
  Stored in directory: /root/.cache/pip/wheels/9b/87/68/41379e7d255d002b3558ec863e1bd0ac87535edf1d3fdc3f64
Successfully built faster-fifo
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 28.1/28.1 MB 59.8 MB/s eta 0:00:00:00:0100:01


In [6]:
!pip install sample-factory==2.0.3

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 721.7/721.7 kB 13.3 MB/s eta 0:00:00a 0:00:01
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
INFO: pip is looking at multiple versions of opencv-python to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.0/9.0 MB 89.1 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.0/63.0 MB 31.3 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 423.2/423.2 kB 30.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 87.2/87.2 kB 7.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 887.4/887.4 MB 2.2 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 317.1/317.1 MB 5.9 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.0/21.0 MB 78.7 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━

In [7]:
import functools

from sample_factory.algo.utils.context import global_model_factory
from sample_factory.cfg.arguments import parse_full_cfg, parse_sf_args
from sample_factory.envs.env_utils import register_env
from sample_factory.train import run_rl

from sf_examples.vizdoom.doom.doom_model import make_vizdoom_encoder
from sf_examples.vizdoom.doom.doom_params import add_doom_env_args, doom_override_defaults
from sf_examples.vizdoom.doom.doom_utils import DOOM_ENVS, make_doom_env_from_spec


# Registers all the ViZDoom environments
def register_vizdoom_envs():
    for env_spec in DOOM_ENVS:
        make_env_func = functools.partial(make_doom_env_from_spec, env_spec)
        register_env(env_spec.name, make_env_func)

# Sample Factory allows the registration of a custom Neural Network architecture
# See https://github.com/alex-petrenko/sample-factory/blob/master/sf_examples/vizdoom/doom/doom_model.py for more details
def register_vizdoom_models():
    global_model_factory().register_encoder_factory(make_vizdoom_encoder)


def register_vizdoom_components():
    register_vizdoom_envs()
    register_vizdoom_models()

# parse the command line args and create a config
def parse_vizdoom_cfg(argv=None, evaluation=False):
    parser, _ = parse_sf_args(argv=argv, evaluation=evaluation)
    # parameters specific to Doom envs
    add_doom_env_args(parser)
    # override Doom default values for algo parameters
    doom_override_defaults(parser)
    # second parsing pass yields the final configuration
    final_cfg = parse_full_cfg(parser, argv)
    return final_cfg

In [8]:
## Start the training, this should take around  minutes
register_vizdoom_components()

env = "doom_health_gathering_supreme"
cfg = parse_vizdoom_cfg(argv=[f"--env={env}",
                              # Argumentos clave modificados
                              "--num_workers=5", # REDUCIDO: Solo necesitamos un worker para renderizar
                              "--train_for_env_steps=50000", # REDUCIDO: 50k pasos es un buen test rápido
                              "--train_for_seconds=36000", # Mantenido, pero los pasos lo limitarán primero

                              
                            
                              # Argumentos originales del modelo (se mantienen)
                              "--restart_behavior=restart",
                              "--num_envs_per_worker=12",
                              "--batch_size=2048",
                              "--recurrence=32",
                              "--exploration_loss_coeff=0.001",
                              "--exploration_loss=symmetric_kl",
                              "--ppo_clip_value=0.2",
                              "--max_grad_norm=0.0",
                              "--obs_scale=255.0",
                              "--decorrelate_experience_max_seconds=1",
                              "--heartbeat_interval=10",
                              "--heartbeat_reporting_interval=300",
                              "--benchmark=false",
                              "--use_rnn=true",
                              "--rnn_type=lstm",
                              "--nonlinearity=relu"
                              ])

status = run_rl(cfg)

[2025-12-01 06:29:05,304][00047] register_encoder_factory: <function make_vizdoom_encoder at 0x7fd04789f240>
[2025-12-01 06:29:05,325][00047] Weights and Biases integration disabled
[2025-12-01 06:29:06,870][00047] Queried available GPUs: 0,1

[2025-12-01 06:29:06,871][00047] Environment var CUDA_VISIBLE_DEVICES is 0,1

[2025-12-01 06:29:08,514][01917] Doom resolution: 160x120, resize resolution: (128, 72)
[2025-12-01 06:29:08,515][01917] Env info: EnvInfo(obs_space=Dict('obs': Box(0, 255, (3, 72, 128), uint8)), action_space=Discrete(5), num_agents=1, gpu_actions=False, gpu_observations=True, action_splits=None, all_discrete=None, frameskip=4, reward_shaping_scheme=None, env_info_protocol_version=1)
[2025-12-01 06:29:08,754][00047] Starting experiment with the following configuration:
help=False
algo=APPO
env=doom_health_gathering_supreme
experiment=default_experiment
train_dir=/kaggle/working/train_dir
restart_behavior=restart
device=gpu
seed=None
num_policies=1
async_rl=True
serial_m

In [9]:
from sample_factory.enjoy import enjoy
register_vizdoom_components()
env = "doom_health_gathering_supreme"
cfg = parse_vizdoom_cfg(argv=[f"--env={env}", "--num_workers=1", "--save_video", "--no_render", "--max_num_episodes=10"], evaluation=True)
status = enjoy(cfg)

[2025-12-01 06:29:38,616][00047] Environment doom_basic already registered, overwriting...
[2025-12-01 06:29:38,617][00047] Environment doom_two_colors_easy already registered, overwriting...
[2025-12-01 06:29:38,618][00047] Environment doom_two_colors_hard already registered, overwriting...
[2025-12-01 06:29:38,618][00047] Environment doom_dm already registered, overwriting...
[2025-12-01 06:29:38,620][00047] Environment doom_dwango5 already registered, overwriting...
[2025-12-01 06:29:38,621][00047] Environment doom_my_way_home_flat_actions already registered, overwriting...
[2025-12-01 06:29:38,622][00047] Environment doom_defend_the_center_flat_actions already registered, overwriting...
[2025-12-01 06:29:38,622][00047] Environment doom_my_way_home already registered, overwriting...
[2025-12-01 06:29:38,623][00047] Environment doom_deadly_corridor already registered, overwriting...
[2025-12-01 06:29:38,624][00047] Environment doom_defend_the_center already registered, overwriting...

In [10]:
from base64 import b64encode
from IPython.display import HTML

mp4 = open('/kaggle/working/train_dir/default_experiment/replay.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=640 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

In [14]:
# 1. Desinstalar la versión conflictiva y instalar la compatible (3.20.x es la más estable para esto)
!pip uninstall -y protobuf
!pip install protobuf==3.20.3

# 2. Reinstalar tensorboard para asegurar que se vincula bien
!pip install --upgrade tensorboard

Found existing installation: protobuf 3.20.3
Uninstalling protobuf-3.20.3:
  Successfully uninstalled protobuf-3.20.3
  Using cached protobuf-3.20.3-py2.py3-none-any.whl.metadata (720 bytes)
Using cached protobuf-3.20.3-py2.py3-none-any.whl (162 kB)
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
bigframes 2.12.0 requires google-cloud-bigquery-storage<3.0.0,>=2.30.0, which is not installed.
opentelemetry-proto 1.37.0 requires protobuf<7.0,>=5.0, but you have protobuf 3.20.3 which is incompatible.
onnx 1.18.0 requires protobuf>=4.25.1, but you have protobuf 3.20.3 which is incompatible.
a2a-sdk 0.3.10 requires protobuf>=5.29.5, but you have protobuf 3.20.3 which is incompatible.
ray 2.51.1 requires click!=8.3.0,>=7.0, but you have click 8.3.0 which is incompatible.
bigframes 2.12.0 requires rich<14,>=12.4.4, but you have rich 14.2.0 which is incompatible.
tensor

In [20]:
import matplotlib.pyplot as plt
import os
import numpy as np
from tensorboard.backend.event_processing.event_accumulator import EventAccumulator

def visualizar_panel_completo(train_dir="train_dir"):
    # 1. Encontrar experimento
    if not os.path.exists(train_dir): return
    all_subdirs = [os.path.join(train_dir, d) for d in os.listdir(train_dir) if os.path.isdir(os.path.join(train_dir, d))]
    exp_path = max(all_subdirs, key=os.path.getmtime)
    
    tfevents_files = [os.path.join(r, f) for r, d, f in os.walk(exp_path) if "tfevents" in f]
    if not tfevents_files: return
    log_file = tfevents_files[0]

    # 2. Cargar datos
    print(f"Graficando datos de: {os.path.basename(log_file)}")
    event_acc = EventAccumulator(log_file, size_guidance={'scalars': 0})
    event_acc.Reload()

    # 3. Definir métricas a graficar
    metrics = [
        {'tag': 'reward/reward', 'title': 'Recompensa Promedio (Rendimiento)', 'color': 'blue'},
        {'tag': 'len/len', 'title': 'Duración del Episodio (Supervivencia)', 'color': 'green'},
        {'tag': 'train/entropy', 'title': 'Entropía (Exploración)', 'color': 'purple'},
        {'tag': 'train/loss', 'title': 'Pérdida Total (Loss)', 'color': 'red'}
    ]

    # 4. Crear subplots (2x2)
    fig, axs = plt.subplots(2, 2, figsize=(15, 10))
    axs = axs.flatten()

    for i, metric in enumerate(metrics):
        try:
            data = event_acc.Scalars(metric['tag'])
            steps = [x.step for x in data]
            values = [x.value for x in data]
            
            # Graficar crudo
            axs[i].plot(steps, values, alpha=0.25, color=metric['color'])
            
            # Graficar suavizado
            if len(values) > 10:
                window = max(5, len(values)//20)
                smoothed = np.convolve(values, np.ones(window)/window, mode='valid')
                valid_steps = steps[:len(smoothed)]
                axs[i].plot(valid_steps, smoothed, color=metric['color'], linewidth=2, label='Tendencia')
            
            axs[i].set_title(metric['title'])
            axs[i].set_xlabel("Pasos")
            axs[i].grid(True, alpha=0.3)
            axs[i].legend()
            
        except KeyError:
            axs[i].set_title(f"{metric['title']} (No encontrado)")
            print(f"Nota: No se encontró la etiqueta {metric['tag']}")

    plt.tight_layout()
    plt.show()

visualizar_panel_completo()